In [1]:
import pandas as pd
import requests
import json
import re
import itertools
import time

In [2]:
df_festival = pd.read_csv('./data/festivals.csv', keep_default_na=False)
df_festival

id                     title_english                title_original  \
0        0                   Adieu Bonaparte                 وداعا بونابرت   
1        1                             Birdy                           N/A   
2        2                             Bliss                           N/A   
3        3              Chicken with Vinegar            Poulet au vinaigre   
4        4                 The Coca-Cola Kid                           N/A   
5        5                      Colonel Redl                   Oberst Redl   
6        6                        Derborence                           N/A   
7        7                         Détective                     Détective   
8        8               Farewell to the Ark                         さらば箱舟   
9        9                    Insignificance                           N/A   
10      10               Joshua Then and Now                           N/A   
11      11          Kiss of the Spider Woman      O Beijo da Mulher Aranha   
12      12                The Official Story           La historia oficial   
13      13                     Madman at War               Scemo di guerra   
14      14                              Mask                           N/A   
15      15  Mishima: A Life in Four Chapters                           N/A   
16      16                        Pale Rider                           N/A   
17      17                       Rendez-vous                           N/A   
18      18    The Two Lives of Mattia Pascal  Le due vite di Mattia Pascal   
19      19  When Father Was Away on Business        Отац на службеном путу   
20      20          The Assassin of the Tsar                  Tsareubiytsa   
21      21                   Anna Karamazoff                           N/A   
22      22                       Barton Fink                           N/A   
23      23                 La Belle Noiseuse                           N/A   
24      24                               Bix                           N/A   
25      25                         Cold Moon                   Lune froide   
26      26      The Double Life of Véronique    La double vie de Véronique   
27      27                            Europa                           N/A   
28      28                         The Flesh                      La carne   
29      29               Guilty by Suspicion                           N/A   
...    ...                               ...                           ...   
4434  4434                   The Long Riders                           N/A   
4435  4435                            Loulou                           N/A   
4436  4436                  The Missing Link                           N/A   
4437  4437              Mon oncle d'Amérique                           N/A   
4438  4438                   Out of the Blue                           N/A   
4439  4439                        Put on Ice                           N/A   
4440  4440           Sauve qui peut (la vie)                           N/A   
4441  4441                 Special Treatment                           N/A   
4442  4442                       La terrazza                           N/A   
4443  4443                 A Week's Vacation                           N/A   
4444  4444                    Apart Together                           N/A   
4445  4445                               Bal                           N/A   
4446  4446                       Caterpillar                           N/A   
4447  4447                        Der Räuber                           N/A   
4448  4448                        En Familie                           N/A   
4449  4449              En ganske snill mann                           N/A   
4450  4450   Eu când vreau să fluier, fluier                           N/A   
4451  4451                         Greenberg                           N/A   
4452  4452                              Howl                           N/A   
4453  4453         Kak ya prov

In [3]:
df_festival.iloc[0:10]

id         title_english      title_original         director  \
0   0       Adieu Bonaparte       وداعا بونابرت  Youssef Chahine   
1   1                 Birdy                 N/A      Alan Parker   
2   2                 Bliss                 N/A     Ray Lawrence   
3   3  Chicken with Vinegar  Poulet au vinaigre   Claude Chabrol   
4   4     The Coca-Cola Kid                 N/A  Dušan Makavejev   
5   5          Colonel Redl         Oberst Redl     István Szabó   
6   6            Derborence                 N/A  Francis Reusser   
7   7             Détective           Détective  Jean-Luc Godard   
8   8   Farewell to the Ark               さらば箱舟   Shūji Terayama   
9   9        Insignificance                 N/A     Nicolas Roeg   

          country  winner festival  year_festival  \
0           Egypt       0   cannes           1985   
1   United States       0   cannes           1985   
2       Australia       0   cannes           1985   
3          France       0   cannes           1985   
4       Australia       0   cannes           1985   
5         Hungary       0   cannes           1985   
6     Switzerland       0   cannes           1985   
7          France       0   cannes           1985   
8           Japan       0   cannes           1985   
9  United Kingdom       0   cannes           1985   

                                           link_film  \
0      https://en.wikipedia.org/wiki/Adieu_Bonaparte   
1         https://en.wikipedia.org/wiki/Birdy_(film)   
2    https://en.wikipedia.org/wiki/Bliss_(1985_film)   
3  https://en.wikipedia.org/wiki/Chicken_with_Vin...   
4    https://en.wikipedia.org/wiki/The_Coca-Cola_Kid   
5         https://en.wikipedia.org/wiki/Colonel_Redl   
6    https://en.wikipedia.org/wiki/Derborence_(film)   
7  https://en.wikipedia.org/wiki/D%C3%A9tective_(...   
8  https://en.wikipedia.org/wiki/Farewell_to_the_Ark   
9  https://en.wikipedia.org/wiki/Insignificance_(...   

                                       link_director  
0      https://en.wikipedia.org/wiki/Youssef_Chahine  
1          https://en.wikipedia.org/wiki/Alan_Parker  
2  https://en.wikipedia.org/wiki/Ray_Lawrence_(fi...  
3       https://en.wikipedia.org/wiki/Claude_Chabrol  
4  https://en.wikipedia.org/wiki/Du%C5%A1an_Makav...  
5  https://en.wikipedia.org/wiki/Istv%C3%A1n_Szab...  
6      https://en.wikipedia.org/wiki/Francis_Reusser  
7      https://en.wikipedia.org/wiki/Jean-Luc_Godard  
8  https://en.wikipedia.org/wiki/Sh%C5%ABji_Terayama  
9         https://en.wikipedia.org/wiki/Nicolas_Roeg

In [4]:
for link in df_festival.iloc[0:10]['link_film']:
    print(link)

https://en.wikipedia.org/wiki/Adieu_Bonaparte
https://en.wikipedia.org/wiki/Birdy_(film)
https://en.wikipedia.org/wiki/Bliss_(1985_film)
https://en.wikipedia.org/wiki/Chicken_with_Vinegar
https://en.wikipedia.org/wiki/The_Coca-Cola_Kid
https://en.wikipedia.org/wiki/Colonel_Redl
https://en.wikipedia.org/wiki/Derborence_(film)
https://en.wikipedia.org/wiki/D%C3%A9tective_(1985_film)
https://en.wikipedia.org/wiki/Farewell_to_the_Ark
https://en.wikipedia.org/wiki/Insignificance_(film)


In [5]:
def get_film_json(key, title1, title2, title3, year):
    titles = [title1, title2, title3]
    years = [year, year-1]
    
    title_year = list(itertools.product(titles, years)) # doesn't work for original titles in languages with certain characters, e.g. Egyptian Arabic 
    
    response = 'False'
    j = 0
    while response == 'False' and j < 6: # 6 because all permutations of 3 titles and 2 years
        url = 'http://www.omdbapi.com/?apikey=' + key + '&t=' + title_year[j][0] + '&y=' + str(title_year[j][1]) + '&plot=full'
        r = requests.get(url)
        film_json = r.json()
        response = film_json['Response']
        j = j + 1
    
    return film_json

In [6]:
def clean_film_json(film_json):
    dict_ratings = {'InternetMovieDatabaseRating': 'N/A',
                    'RottenTomatoesRating': 'N/A',
                    'MetacriticRating': 'N/A'}

    source = [rating['Source'].replace(' ', '') + 'Rating' for rating in film_json['Ratings']]
    value = [rating['Value'] for rating in film_json['Ratings']]

    for i in range(len(source)):
        dict_ratings[source[i]] = value[i]

    film_json.pop('Ratings')
    film_json.update(dict_ratings)
    
    return film_json

In [7]:
credentials = pd.read_csv('credentials.csv')
omdbapikey = credentials['omdbapikey'][0]
regex_paren = '_\((.*film.*)\)'

for i in df_festival['id']:
# for i in range(10):
    t0 = time.time()
    
    title_link = df_festival.iloc[i]['link_film']
    title_link = title_link.replace('https://en.wikipedia.org/wiki/', '')
    title_link = re.sub(regex_paren, '', title_link.replace('https://en.wikipedia.org/wiki/', ''))
    title_link = title_link.replace('_', '+')
    title_english = df_festival.iloc[i]['title_english'].replace(' ', '+')
    title_original = df_festival.iloc[i]['title_original'].replace(' ', '+')
    print(i)
    print(title_link)
    
    year_festival = df_festival.iloc[i]['year_festival']
    
    film_json = get_film_json(omdbapikey, title_link, title_english, title_original, year_festival)
    film_json = clean_film_json(film_json) if film_json['Response'] == 'True' else film_json
    
    with open('./data/json/' + str(i) + '.json', 'w') as file:
        json.dump(film_json, file)
    
    print(film_json)
    
    response_delay = time.time() - t0
    print(10*response_delay)
    print('\n')
    time.sleep(10*response_delay)

0
Adieu+Bonaparte
{'Title': 'Adieu Bonaparte', 'Year': '1985', 'Rated': 'N/A', 'Released': '17 May 1985', 'Runtime': '115 min', 'Genre': 'Drama, History, War', 'Director': 'Youssef Chahine', 'Writer': 'Youssef Chahine, Yusri Nasrullah', 'Actors': 'Michel Piccoli, Mohsen Mohieddin, Patrice Chéreau, Mohamad Atef', 'Plot': 'A story during the French Occupation of Egypt (1797-1803), depicting the conflict between tradintion and modernization in the context of fighting the French invadors.', 'Language': 'French, Arabic', 'Country': 'Egypt, France', 'Awards': '1 nomination.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BYWRjOTNhNDQtY2M4OS00YzM0LWI5NTctNzU1ZWI2ZmRjODRhXkEyXkFqcGdeQXVyMzI4MTk3MTY@._V1_SX300.jpg', 'Metascore': 'N/A', 'imdbRating': '6.4', 'imdbVotes': '236', 'imdbID': 'tt0088383', 'Type': 'movie', 'DVD': 'N/A', 'BoxOffice': 'N/A', 'Production': 'N/A', 'Website': 'N/A', 'Response': 'True', 'InternetMovieDatabaseRating': '6.4/10', 'RottenTomatoesRating': 'N/A', 'MetacriticRa

8
Farewell+to+the+Ark
{'Title': 'Farewell to the Ark', 'Year': '1984', 'Rated': 'N/A', 'Released': '08 Sep 1984', 'Runtime': '127 min', 'Genre': 'Fantasy, Mystery, Romance', 'Director': 'Shûji Terayama', 'Writer': 'Gabriel García Márquez (novel), Rio Kishida, Shûji Terayama', 'Actors': 'Tsutomu Yamazaki, Mayumi Ogawa, Yoshio Harada, Yôko Takahashi', 'Plot': 'A surreal, isolated village sees its inhabitants gradually leave behind their mutual traditions and superstitions as they leave for the city. Among them are two cousins who love each other and who get into a quarrel with other villagers.', 'Language': 'Japanese', 'Country': 'Japan', 'Awards': '7 wins & 2 nominations.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BZmFhM2Y0MzYtMjc1MS00NTEwLTkzMjUtNGU3ZTljZjQ2NGFkXkEyXkFqcGdeQXVyMzU0NzkwMDg@._V1_SX300.jpg', 'Metascore': 'N/A', 'imdbRating': '7.4', 'imdbVotes': '251', 'imdbID': 'tt0088041', 'Type': 'movie', 'DVD': 'N/A', 'BoxOffice': 'N/A', 'Production': 'N/A', 'Website': 'N/A', 

15
Mishima:+A+Life+in+Four+Chapters
{'Title': 'Mishima: A Life in Four Chapters', 'Year': '1985', 'Rated': 'R', 'Released': '20 Sep 1985', 'Runtime': '120 min', 'Genre': 'Biography, Drama', 'Director': 'Paul Schrader', 'Writer': 'Paul Schrader, Leonard Schrader', 'Actors': 'Ken Ogata, Masayuki Shionoya, Hiroshi Mikami, Junya Fukuda', 'Plot': 'A fictionalized account in four segments of the life of Japan\'s celebrated twentieth-century author Yukio Mishima. Three of the segments parallel events in Mishima\'s life with his novels (The Temple of the Golden Pavilion (Kinkaku-ji), Kyoko\'s House, and Runaway Horses), while the fourth depicts 25 November 1970, "The Last Day"...', 'Language': 'Japanese, English', 'Country': 'USA, Japan', 'Awards': '1 win & 1 nomination.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BNDM2NWU1NWEtYzBmNC00MDA4LWI2YzQtZTQ1Y2E3NjZhMDJjXkEyXkFqcGdeQXVyNTAyODkwOQ@@._V1_SX300.jpg', 'Metascore': '81', 'imdbRating': '7.9', 'imdbVotes': '7,681', 'imdbID': 'tt00896

23
La+Belle+Noiseuse
{'Title': 'La Belle Noiseuse', 'Year': '1991', 'Rated': 'Unrated', 'Released': '04 Sep 1991', 'Runtime': '238 min', 'Genre': 'Drama', 'Director': 'Jacques Rivette', 'Writer': 'Pascal Bonitzer (scenario), Christine Laurent (scenario), Jacques Rivette (scenario), Honoré de Balzac (inspired by novella "Le chef-d\'oeuvre inconnu"), Pascal Bonitzer (dialogue), Christine Laurent (dialogue)', 'Actors': 'Michel Piccoli, Jane Birkin, Emmanuelle Béart, Marianne Denicourt', 'Plot': "The former famous painter Frenhofer lives quietly with his wife in his countryside residence in the French Provence. When the young artist Nicolas visits him with his girlfriend Marianne, Frenhofer decides to start working again on a painting called 'La Belle Noiseuse', which he gave up a long time ago. And he wants Marianne as a model. The ensuing creative process will change the characters' lives. It will become a struggle for truth and meaning, and the question about the limits of art will aris

29
Guilty+by+Suspicion
{'Title': 'Guilty by Suspicion', 'Year': '1991', 'Rated': 'PG-13', 'Released': '15 Mar 1991', 'Runtime': '105 min', 'Genre': 'Drama', 'Director': 'Irwin Winkler', 'Writer': 'Irwin Winkler', 'Actors': 'Robert De Niro, Annette Bening, George Wendt, Patricia Wettig', 'Plot': 'David Merrill (Robert De Niro), a fictitious 1950s Hollywood director, returns from filming abroad in France to find that his loyalty has been called into question by the House Committee on Un-American Activities and he is unable to work until cleared. Before being called, his highest priority had been his work to the extent of leaving his wife (Annette Bening) and son (Luke Edwards) alone for months at a time. He initially refuses to implicate others or himself in a private meeting with Roy Cohn and a studio lawyer. This decision initially to stick to his principles first leaves him unable to work in his profession, even with films and producers he never would have worked with before. Harassme

...

732
N/A
{'Title': 'A Estrangeira', 'Year': '1982', 'Rated': 'N/A', 'Released': '04 Mar 1983', 'Runtime': '100 min', 'Genre': 'Drama', 'Director': 'João Mário Grilo', 'Writer': 'Teresa Azevedo, Michael Graham, João Mário Grilo', 'Actors': 'Fernando Rey, Teresa Madruga, Carole Courtoy, Mariana Villar', 'Plot': 'N/A', 'Language': 'Portuguese', 'Country': 'Portugal', 'Awards': '1 nomination.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BZWE2YzQ2Y2EtZmM1Mi00ZDg1LWFiMTUtNzQxODVkMWNkZjRiXkEyXkFqcGdeQXVyNDg5MjMyMTM@._V1_SX300.jpg', 'Metascore': 'N/A', 'imdbRating': '7.1', 'imdbVotes': '12', 'imdbID': 'tt0083904', 'Type': 'movie', 'DVD': 'N/A', 'BoxOffice': 'N/A', 'Production': 'N/A', 'Website': 'N/A', 'Response': 'True', 'InternetMovieDatabaseRating': '7.1/10', 'RottenTomatoesRating': 'N/A', 'MetacriticRating': 'N/A'}
6.525449752807617


733
Le+Beau+Mariage
{'Title': 'A Good Marriage', 'Year': '1982', 'Rated': 'PG', 'Released': '27 Aug 1982', 'Runtime': '93 min', 'Genre': 'Comedy, Drama

741
Private+Life
{'Title': 'Chastnaya zhizn', 'Year': '1982', 'Rated': 'N/A', 'Released': '23 Aug 1982', 'Runtime': '102 min', 'Genre': 'Drama', 'Director': 'Yuli Raizman', 'Writer': 'Anatoli Grebnev, Yuli Raizman', 'Actors': 'Mikhail Ulyanov, Iya Savvina, Irina Gubanova, Tatyana Dogileva', 'Plot': 'A man gets fired from his cooshie government job. He thinks its the end of the world but slowly finds things to live for. Nominated for Oscar in the foreign language movie category.', 'Language': 'Russian', 'Country': 'Soviet Union', 'Awards': 'Nominated for 1 Oscar. Another 1 win & 1 nomination.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BMWJhYjk3MjItNzg1OC00ZmJiLWE2OTMtYTBmMTAwNzNhZTMzXkEyXkFqcGdeQXVyMTc4MzI2NQ@@._V1_SX300.jpg', 'Metascore': 'N/A', 'imdbRating': '7.1', 'imdbVotes': '137', 'imdbID': 'tt0083732', 'Type': 'movie', 'DVD': 'N/A', 'BoxOffice': 'N/A', 'Production': 'N/A', 'Website': 'N/A', 'Response': 'True', 'InternetMovieDatabaseRating': '7.1/10', 'RottenTomatoesRatin

749
Careful,+He+Might+Hear+You
{'Title': 'Careful, He Might Hear You', 'Year': '1983', 'Rated': 'PG', 'Released': '15 Jun 1984', 'Runtime': '110 min', 'Genre': 'Drama', 'Director': 'Carl Schultz', 'Writer': 'Sumner Locke Elliott (novel), Michael Jenkins', 'Actors': 'Wendy Hughes, Robyn Nevin, Nicholas Gledhill, John Hargreaves', 'Plot': "His mother dead, PS lives in Sydney with working-class Aunt Lila and Uncle George. When he's six or eight, his posh Aunt Vanessa descends from England. Named a co-guardian by PS's feckless, absent father, she asserts her rights and convinces Lila to have PS live with her weekdays. PS is happy at Lila's, playing with children, running about, speaking up. At Vanessa's, there's a regimen of private school, round vowels, piano and riding lessons, and lonely indoor play with fancy toys. He's miserable and when he objects, she sues for complete custody. Will anyone listen to him? And will he take on Vanessa's challenges to find out who he is and to love some

{'Response': 'False', 'Error': 'Movie not found!'}
5.60978889465332


757
N/A
{'Response': 'False', 'Error': 'Request limit reached!'}
5.1065993309021


758
Life+Is+a+Bed+of+Roses
{'Response': 'False', 'Error': 'Request limit reached!'}
13.352789878845215


759
A+Love+in+Germany
{'Response': 'False', 'Error': 'Request limit reached!'}
7.226769924163818


760
Maria+Chapdelaine
{'Response': 'False', 'Error': 'Movie not found!'}
5.304059982299805


761
The+Millennial+Bee
{'Response': 'False', 'Error': 'Request limit reached!'}
7.315559387207031


762
Mother+Mary
{'Response': 'False', 'Error': 'Request limit reached!'}
7.340662479400635


763
N/A
{'Response': 'False', 'Error': 'Request limit reached!'}
7.576198577880859


764
A+School+Outing
{'Response': 'False', 'Error': 'Request limit reached!'}
7.698700428009033


765
N/A
{'Response': 'False', 'Error': 'Request limit reached!'}
7.062492370605469


766
Streamers
{'Response': 'False', 'Error': 'Movie not found!'}
5.447759628295898


767
S

KeyboardInterrupt: 

In [7]:
credentials = pd.read_csv('credentials.csv')
omdbapikey = credentials['omdbapikey'][0]
regex_paren = '_\((.*film.*)\)'

# for i in df_festival['id']:
for i in range(755, len(df_festival['id'])):
    t0 = time.time()
    
    title_link = df_festival.iloc[i]['link_film']
    title_link = title_link.replace('https://en.wikipedia.org/wiki/', '')
    title_link = re.sub(regex_paren, '', title_link.replace('https://en.wikipedia.org/wiki/', ''))
    title_link = title_link.replace('_', '+')
    title_english = df_festival.iloc[i]['title_english'].replace(' ', '+')
    title_original = df_festival.iloc[i]['title_original'].replace(' ', '+')
    print(i)
    print(title_link)
    
    year_festival = df_festival.iloc[i]['year_festival']
    
    film_json = get_film_json(omdbapikey, title_link, title_english, title_original, year_festival)
    film_json = clean_film_json(film_json) if film_json['Response'] == 'True' else film_json
    
    with open('./data/json/' + str(i) + '.json', 'w') as file:
        json.dump(film_json, file)
    
    print(film_json)
    
    response_delay = time.time() - t0
    print(10*response_delay)
    print('\n')
    time.sleep(10*response_delay)

# INCORRECT: 1390 Via Castellana Bandiera, 1394 Birdman, 1424 Per amor vostro

755
Hanna+K.
{'Title': 'Hanna K.', 'Year': '1983', 'Rated': 'R', 'Released': 'N/A', 'Runtime': '111 min', 'Genre': 'Drama', 'Director': 'Costa-Gavras', 'Writer': 'Franco Solinas (original scenario), Costa-Gavras (original scenario), Franco Solinas', 'Actors': 'Jill Clayburgh, Jean Yanne, Gabriel Byrne, Mohammad Bakri', 'Plot': "Hanna Kaufman is a Jewish-American, who moved to Israel and now works as a defense lawyer there. Her troubles start when she's court-appointed to defend Palestinian Salim Bakri, who's been arrested and charged by the military tribunal with belonging to a terrorist network. Bakri claims that he's an innocent victim of prosecution by the Israeli state, because he wants his family's property back. Hanna investigates his claims and realizes that he may not be lying. The prosecutor proposes a way to both get rid of Bakri and not give in to his demands. Hanna must decide whether to give in and possibly save her client's life or fight for what she, as the child of Holo

761
The+Millennial+Bee
{'Title': 'The Millennial Bee', 'Year': '1983', 'Rated': 'N/A', 'Released': '01 Mar 1984', 'Runtime': '162 min', 'Genre': 'Comedy, Drama, War', 'Director': 'Juraj Jakubisko', 'Writer': 'Juraj Jakubisko, Peter Jaros (novel), Peter Jaros (screenplay)', 'Actors': 'Jozef Kroner, Stefan Kvietik, Michal Docolomanský, Jana Janovská', 'Plot': "A historic mega-film, one family saga, three generations (1887 -1917) assimilated to the bee community in the hive. The queen bee serves as a big mother that symbolizes the family and national roots, the power and meaning of tradition and the return to it. The mosaic of the bricklaying Pichanda family's lives is made of love, hope, hard work, human understanding and also the tragedies of economic crisis, war and human malice. Dreams, symbols, and life in all its forms create a colored rainbow spanning from birth to death and from mystery to reality and back.", 'Language': 'Slovak, Czech, Hungarian', 'Country': 'Czechoslovakia, West

769
N/A
{'Title': 'Angelas krig', 'Year': '1984', 'Rated': 'N/A', 'Released': '07 Sep 1984', 'Runtime': '97 min', 'Genre': 'Drama, War', 'Director': 'Eija-Elina Bergholm', 'Writer': 'Eija-Elina Bergholm, Jörn Donner (novel)', 'Actors': 'Ida-Lotta Backman, Mathieu Carrière, Jörn Donner, Kim Gunell', 'Plot': 'Angela serves during the so-called Finnish winter war (1939-1940) as a nurse at a war hospital. There she meets Thomas Schmidt, a German officer who, in part, lost his memory due to her injuries. They fall in love.', 'Language': 'Swedish, English, Latin, Finnish, German', 'Country': 'Finland, Sweden, West Germany', 'Awards': '1 win & 1 nomination.', 'Poster': 'N/A', 'Metascore': 'N/A', 'imdbRating': '5.5', 'imdbVotes': '29', 'imdbID': 'tt0086897', 'Type': 'movie', 'DVD': 'N/A', 'BoxOffice': 'N/A', 'Production': 'N/A', 'Website': 'N/A', 'Response': 'True', 'InternetMovieDatabaseRating': '5.5/10', 'RottenTomatoesRating': 'N/A', 'MetacriticRating': 'N/A'}
8.61412763595581


770
The+Ann

778
Love+Unto+Death
{'Title': 'Love Unto Death', 'Year': '1984', 'Rated': 'Not Rated', 'Released': '05 Sep 1984', 'Runtime': '92 min', 'Genre': 'Drama, Romance', 'Director': 'Alain Resnais', 'Writer': 'Jean Gruault (scenario)', 'Actors': 'Sabine Azéma, Fanny Ardant, Pierre Arditi, André Dussollier', 'Plot': 'Elisabeth and Simon have been deeply in love for two months when Simon momentarily dies, but comes back to life. Simon does not want any further medical tests, but the couple are forced to grapple with the possibility of his death. They eventually tell their close friends Jérôme and Judith Martignac about the event. The Martignacs are both clerics, and Judith has just been giving a funeral service for a villager who committed suicide, though Jérôme would have nothing to do with suicide...', 'Language': 'French', 'Country': 'France', 'Awards': '6 nominations.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BNTEzNTE4MGYtZmM3NS00M2RjLWFjYmYtNmI1Nzc1NjMwZWQzXkEyXkFqcGdeQXVyMzIwNDY4

786
N/A
{'Title': 'Bereg', 'Year': '1984', 'Rated': 'N/A', 'Released': '01 May 1986', 'Runtime': '141 min', 'Genre': 'Romance', 'Director': 'Aleksandr Alov, Vladimir Naumov', 'Writer': 'Aleksandr Alov, Yuri Bondarev (novel), Yuri Bondarev (screenplay), Vladimir Naumov', 'Actors': 'Boris Shcherbakov, Natalya Belokhvostikova, Bernhard Wicki, Vladimir Gostyukhin', 'Plot': 'N/A', 'Language': 'Russian', 'Country': 'Soviet Union, West Germany', 'Awards': '1 nomination.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BNDk3MDc3OWUtMWU4Mi00ODJlLWFkMzItYmRjZDc3NmI0YmM4XkEyXkFqcGdeQXVyMzU0NzkwMDg@._V1_SX300.jpg', 'Metascore': 'N/A', 'imdbRating': '7.2', 'imdbVotes': '46', 'imdbID': 'tt0086951', 'Type': 'movie', 'DVD': 'N/A', 'BoxOffice': 'N/A', 'Production': 'N/A', 'Website': 'N/A', 'Response': 'True', 'InternetMovieDatabaseRating': '7.2/10', 'RottenTomatoesRating': 'N/A', 'MetacriticRating': 'N/A'}
9.170939922332764


787
Sonatine
{'Title': 'Sonatine', 'Year': '1984', 'Rated': 'N/A', 'Releas

...

1409
Red+Amnesia
{'Title': 'Red Amnesia', 'Year': '2014', 'Rated': 'N/A', 'Released': '30 Apr 2015', 'Runtime': '116 min', 'Genre': 'Crime, Drama, Thriller', 'Director': 'Xiaoshuai Wang', 'Writer': 'Xiaoshuai Wang (screenplay), Lei Fang (screenplay), Fei Li (screenplay)', 'Actors': 'Zhong Lü, Yuanzheng Feng, Hailu Qin, Hao Qin', 'Plot': 'Deng is a stubborn retired widow who spends her days caring about her two grown up sons and her elderly mother, despite her family efforts to stop her. But her daily routine starts derailing when she keeps receiving anonymous calls..', 'Language': 'Mandarin', 'Country': 'China', 'Awards': '3 wins & 8 nominations.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BNDMyNDI2ODEwMl5BMl5BanBnXkFtZTgwMjAyODIzMjE@._V1_SX300.jpg', 'Metascore': 'N/A', 'imdbRating': '6.9', 'imdbVotes': '410', 'imdbID': 'tt3890278', 'Type': 'movie', 'DVD': 'N/A', 'BoxOffice': 'N/A', 'Production': 'N/A', 'Website': 'N/A', 'Response': 'True', 'InternetMovieDatabaseRating': '6.9/1

1417
A+Bigger+Splash
{'Title': 'A Bigger Splash', 'Year': '2015', 'Rated': 'R', 'Released': '13 May 2016', 'Runtime': '125 min', 'Genre': 'Drama, Thriller', 'Director': 'Luca Guadagnino', 'Writer': 'David Kajganich (screenplay by), Jacques Deray (based on the film "La piscine" directed by), Alain Page (based on an original screenplay by), Alain Page (based on his novel "La piscine"), Jacques Deray (adaption by), Jean-Claude Carrière (adaption by), Jacques Deray (dialogue by), Jean-Claude Carrière (dialogue by)', 'Actors': 'Tilda Swinton, Matthias Schoenaerts, Ralph Fiennes, Dakota Johnson', 'Plot': 'In A BIGGER SPLASH, the lives of a high profile couple, a famous rock star (Tilda Swinton) and a filmmaker (Matthias Schoenaerts), vacationing and recovering on the idyllic sun-drenched and remote Italian island of Pantelleria, are disrupted by the unexpected visit of an old friend (Ralph Fiennes) and his daughter (Dakota Johnson) - creating a whirlwind of jealousy, passion and, ultimately,

1423
Equals
{'Title': 'Equals', 'Year': '2015', 'Rated': 'PG-13', 'Released': '26 May 2016', 'Runtime': '101 min', 'Genre': 'Drama, Romance, Sci-Fi', 'Director': 'Drake Doremus', 'Writer': 'Nathan Parker (screenplay by), Drake Doremus (story by)', 'Actors': 'Nicholas Hoult, Vernetta Lopez, Scott Lawrence, Kate Lyn Sheil', 'Plot': 'A futuristic love story set in a world where emotions have been eradicated.', 'Language': 'English', 'Country': 'USA, Indonesia', 'Awards': '1 win & 5 nominations.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BMTg3NTQ5MDU3OF5BMl5BanBnXkFtZTgwODc2Mzk5NzE@._V1_SX300.jpg', 'Metascore': '43', 'imdbRating': '6.1', 'imdbVotes': '25,381', 'imdbID': 'tt3289728', 'Type': 'movie', 'DVD': '06 Sep 2016', 'BoxOffice': 'N/A', 'Production': 'A24 and DIRECTV', 'Website': 'N/A', 'Response': 'True', 'InternetMovieDatabaseRating': '6.1/10', 'RottenTomatoesRating': '35%', 'MetacriticRating': '43/100'}
1.7023491859436035


1424
Per+amor+vostro
{'Title': 'Bay Uno: Wait for 

1431
Rabin,+the+Last+Day
{'Title': 'Rabin, the Last Day', 'Year': '2015', 'Rated': 'Not Rated', 'Released': '05 Nov 2015', 'Runtime': '153 min', 'Genre': 'Drama, History', 'Director': 'Amos Gitai', 'Writer': 'Amos Gitai, Marie-Jose Sanselme', 'Actors': 'Ischac Hiskiya, Yitzhak Hizkiya, Pini Mittelman, Michael Warshaviak', 'Plot': "Itzhak Rabin's murder ended all efforts of peace, and with him the whole left wing of Israel died. The movie shows the last of his days as prime minister, and what led to his murder.", 'Language': 'English, Hebrew', 'Country': 'Israel, France', 'Awards': '4 wins & 4 nominations.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BMjUyODExZDAtMWVhZi00YjkxLTg1MmQtOGIxZTM2MzIwMjIzXkEyXkFqcGdeQXVyMjMyMzI4MzY@._V1_SX300.jpg', 'Metascore': '66', 'imdbRating': '5.9', 'imdbVotes': '336', 'imdbID': 'tt4935282', 'Type': 'movie', 'DVD': 'N/A', 'BoxOffice': 'N/A', 'Production': 'N/A', 'Website': 'N/A', 'Response': 'True', 'InternetMovieDatabaseRating': '5.9/10', 'Rotten

KeyboardInterrupt: 

In [7]:
credentials = pd.read_csv('credentials.csv')
omdbapikey = credentials['omdbapikey'][0]
regex_paren = '_\((.*film.*)\)'

# for i in df_festival['id']:
for i in range(1432, len(df_festival['id'])):
    t0 = time.time()
    
    title_link = df_festival.iloc[i]['link_film']
    title_link = title_link.replace('https://en.wikipedia.org/wiki/', '')
    title_link = re.sub(regex_paren, '', title_link.replace('https://en.wikipedia.org/wiki/', ''))
    title_link = title_link.replace('_', '+')
    title_english = df_festival.iloc[i]['title_english'].replace(' ', '+')
    title_original = df_festival.iloc[i]['title_original'].replace(' ', '+')
    print(i)
    print(title_link)
    
    year_festival = df_festival.iloc[i]['year_festival']
    
    film_json = get_film_json(omdbapikey, title_link, title_english, title_original, year_festival)
    film_json = clean_film_json(film_json) if film_json['Response'] == 'True' else film_json
    
    with open('./data/json/' + str(i) + '.json', 'w') as file:
        json.dump(film_json, file)
    
    print(film_json)
    
    response_delay = time.time() - t0
    print(10*response_delay)
    print('\n')
    time.sleep(10*response_delay)
    
# INCORRECT: 2593 The Sea, 2610 Félix et Lola (manual)

1432
Remember
{'Title': 'Remember', 'Year': '2015', 'Rated': 'R', 'Released': '17 Dec 2015', 'Runtime': '94 min', 'Genre': 'Drama, Mystery, Thriller', 'Director': 'Atom Egoyan', 'Writer': 'Benjamin August', 'Actors': 'Christopher Plummer, Kim Roberts, Amanda Smith, Martin Landau', 'Plot': '"Remember" is the contemporary story of Zev, who discovers that the Nazi guard who murdered his family some 70 years ago is living in America under an assumed identity. Despite the obvious challenges, Zev sets out on a mission to deliver long-delayed justice with his own trembling hand. What follows is a remarkable cross-continent road-trip with surprising consequences.', 'Language': 'English, German', 'Country': 'Canada, Mexico, Germany, South Africa', 'Awards': '4 wins & 24 nominations.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BMjM3OTY3Njc1OV5BMl5BanBnXkFtZTgwNDY0MzE1NzE@._V1_SX300.jpg', 'Metascore': '52', 'imdbRating': '7.5', 'imdbVotes': '20,824', 'imdbID': 'tt3704050', 'Type': 'movie'

1439
The+Distinguished+Citizen
{'Title': 'The Distinguished Citizen', 'Year': '2016', 'Rated': 'N/A', 'Released': '01 Sep 2017', 'Runtime': '118 min', 'Genre': 'Comedy, Drama', 'Director': 'Gastón Duprat(co-director), Mariano Cohn(co-director)', 'Writer': 'Andrés Duprat', 'Actors': 'Oscar Martínez, Dady Brieva, Andrea Frigerio, Nora Navas', 'Plot': 'After refusing big and prestigious awards all over the world, Mr. Mantovani, Literature Nobel Prize winner, accepts an invitation to visit his hometown in Argentina, which has been the inspiration for all of his books. It turns out that accepting this invitation is the worse idea of his life. Expect the unexpected when you have used real people as characters in your novels!', 'Language': 'Spanish', 'Country': 'Argentina, Spain', 'Awards': '28 wins & 20 nominations.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BNmQ2OTcwZTItNmM2Yy00YWY1LWJhMmMtY2E3NjcxODZhYWRkXkEyXkFqcGdeQXVyNzcxNDE1MzI@._V1_SX300.jpg', 'Metascore': 'N/A', 'imdbRating'

1445
On+the+Milky+Road
{'Title': 'On the Milky Road', 'Year': '2016', 'Rated': 'N/A', 'Released': '25 Feb 2017', 'Runtime': '125 min', 'Genre': 'Comedy, Drama, Fantasy, Romance, War', 'Director': 'Emir Kusturica', 'Writer': 'Emir Kusturica (screenplay)', 'Actors': "Emir Kusturica, Monica Bellucci, Sloboda Micalovic, Predrag 'Miki' Manojlovic", 'Plot': 'A story that stretches across war, blossoming love and living as a recluse.', 'Language': 'Serbian, Italian', 'Country': 'Serbia, UK, USA', 'Awards': '3 wins & 2 nominations.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BMjA1MjI3MTI2NF5BMl5BanBnXkFtZTgwNjY0Njg5MTE@._V1_SX300.jpg', 'Metascore': 'N/A', 'imdbRating': '6.4', 'imdbVotes': '3,409', 'imdbID': 'tt2800340', 'Type': 'movie', 'DVD': 'N/A', 'BoxOffice': 'N/A', 'Production': 'N/A', 'Website': 'N/A', 'Response': 'True', 'InternetMovieDatabaseRating': '6.4/10', 'RottenTomatoesRating': '50%', 'MetacriticRating': 'N/A'}
1.3837790489196777


1446
Paradise
{'Title': 'Paradise', 'Yea

1452
The+Woman+Who+Left
{'Title': 'The Woman Who Left', 'Year': '2016', 'Rated': 'TV-MA', 'Released': '28 Sep 2016', 'Runtime': '226 min', 'Genre': 'Drama', 'Director': 'Lav Diaz', 'Writer': 'Lav Diaz (screenplay), Leo Tolstoy (inspired by his short story "God Sees the Truth,  But Waits")', 'Actors': 'Charo Santos-Concio, John Lloyd Cruz, Michael De Mesa, Nonie Buencamino', 'Plot': 'After 30 years of wrongful imprisonment, a woman plans to take revenge on her former lover.', 'Language': 'Filipino, Tagalog, English, Japanese', 'Country': 'Philippines', 'Awards': '3 wins & 25 nominations.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BODFjNjg2ZWEtMjlhOS00MjU0LWFhYTItNDkwYzQyMGU1NTFhXkEyXkFqcGdeQXVyODM3MjA1NA@@._V1_SX300.jpg', 'Metascore': '83', 'imdbRating': '7.3', 'imdbVotes': '1,097', 'imdbID': 'tt5843990', 'Type': 'movie', 'DVD': 'N/A', 'BoxOffice': 'N/A', 'Production': 'N/A', 'Website': 'N/A', 'Response': 'True', 'InternetMovieDatabaseRating': '7.3/10', 'RottenTomatoesRating': 

1461
Foxtrot
{'Title': 'Foxtrot', 'Year': '2017', 'Rated': 'R', 'Released': '21 Sep 2017', 'Runtime': '113 min', 'Genre': 'Drama', 'Director': 'Samuel Maoz', 'Writer': 'Samuel Maoz', 'Actors': 'Lior Ashkenazi, Sarah Adler, Yonaton Shiray, Shira Haas', 'Plot': "A troubled family must face the facts when something goes terribly wrong at their son's desolate military post.", 'Language': 'Hebrew, German', 'Country': 'Israel, Switzerland, Germany, France', 'Awards': '19 wins & 20 nominations.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BYjkxY2ZkM2UtYmRmOS00MWYzLTg4NjktY2MzZjU0MjU0YTc1XkEyXkFqcGdeQXVyMTMxODk2OTU@._V1_SX300.jpg', 'Metascore': '88', 'imdbRating': '7.3', 'imdbVotes': '5,503', 'imdbID': 'tt6896536', 'Type': 'movie', 'DVD': 'N/A', 'BoxOffice': '$36,786', 'Production': 'Sony Pictures Classics', 'Website': 'N/A', 'Response': 'True', 'InternetMovieDatabaseRating': '7.3/10', 'RottenTomatoesRating': '94%', 'MetacriticRating': '88/100'}
1.6980981826782227


1462
Hannah
{'Title'

...

2587
https://en.wikipedia.org/w/index.php?title=Boy%27s+Choir&action=edit&redlink=1
{'Title': "Boy's Choir", 'Year': '2000', 'Rated': 'N/A', 'Released': '10 Feb 2000', 'Runtime': '129 min', 'Genre': 'Drama, Music', 'Director': 'Akira Ogata', 'Writer': 'Kenji Aoki', 'Actors': 'Atsushi Itô, Sora Tôma, Teruyuki Kagawa, Ryoko Takizawa', 'Plot': 'The lives of two orphan boys begin to intertwine when the choir and the feelings they share bring them closer to one another.', 'Language': 'Japanese', 'Country': 'Japan', 'Awards': '11 wins & 1 nomination.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BMjA5NzM0Mzg5M15BMl5BanBnXkFtZTcwMzYwMTczMQ@@._V1_SX300.jpg', 'Metascore': 'N/A', 'imdbRating': '6.6', 'imdbVotes': '193', 'imdbID': 'tt0233595', 'Type': 'movie', 'DVD': '17 Jun 2003', 'BoxOffice': 'N/A', 'Production': 'N/A', 'Website': 'N/A', 'Response': 'True', 'InternetMovieDatabaseRating': '6.6/10', 'RottenTomatoesRating': 'N/A', 'MetacriticRating': 'N/A'}
5.182919502258301


2588
The+Road+

2594
The+Million+Dollar+Hotel
{'Title': 'The Million Dollar Hotel', 'Year': '2000', 'Rated': 'R', 'Released': '10 Feb 2000', 'Runtime': '122 min', 'Genre': 'Drama, Mystery, Thriller', 'Director': 'Wim Wenders', 'Writer': 'Bono (story), Nicholas Klein (screenplay), Nicholas Klein (story)', 'Actors': 'Jeremy Davies, Milla Jovovich, Mel Gibson, Jimmy Smits', 'Plot': "The Million Dollar Hotel follows the supposed murder of Izzy Goldkiss. FBI Agent Skinner is sent into investigate the crime, and to weed out the killer. When he reaches the 'hotel', he comes across many of the forgotten types of people living in the city. You have Geronimo, who is a self proclaimed Native American artist. Dixie, played with great gusto by Peter Stormare, as the 'fifth' Beetle that is still waiting for his royalty payments, as well as recognition. Eloise, who is the neighborhood 'whore'. And then there is Tom-Tom, played by Jeremy Davies. He's the center of the story, being that he's the 'village idiot' of the

2601
The+Legend+of+Rita
{'Title': 'The Legend of Rita', 'Year': '2000', 'Rated': 'N/A', 'Released': '14 Sep 2000', 'Runtime': '103 min', 'Genre': 'Drama, Romance', 'Director': 'Volker Schlöndorff', 'Writer': 'Wolfgang Kohlhaase, Volker Schlöndorff', 'Actors': 'Bibiana Beglau, Martin Wuttke, Nadja Uhl, Harald Schrott', 'Plot': 'Rita Vogt is a radical West German terrorist who abandons the revolution and settles in East Germany with a new identity provided by the East German secret service. She lives in constant fear of having her cover blown, which unavoidably happens after the German re-unification.', 'Language': 'German, French, English', 'Country': 'Germany', 'Awards': '4 wins & 5 nominations.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BNDM0MzMwMTQ0MF5BMl5BanBnXkFtZTcwMDk2NjUxMQ@@._V1_SX300.jpg', 'Metascore': 'N/A', 'imdbRating': '7.0', 'imdbVotes': '1,977', 'imdbID': 'tt0234805', 'Type': 'movie', 'DVD': '09 Oct 2001', 'BoxOffice': 'N/A', 'Production': 'Kino International', 

2609
Chocolat
{'Title': 'Crème glacée, chocolat et autres consolations', 'Year': '2001', 'Rated': 'G', 'Released': '31 Aug 2001', 'Runtime': '97 min', 'Genre': 'Drama, Comedy, Romance', 'Director': 'Julie Hivon', 'Writer': 'Julie Hivon', 'Actors': 'Dorothée Berryman, Geneviève Bilodeau, Isabelle Brouillette, France Castel', 'Plot': 'N/A', 'Language': 'French', 'Country': 'Canada', 'Awards': '1 nomination.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BM2Y3NTRjMjUtNWExMS00NDA4LWFlNjMtZDQyMTUwYWEwMTExXkEyXkFqcGdeQXVyNTA1NDY3NzY@._V1_SX300.jpg', 'Metascore': 'N/A', 'imdbRating': '6.8', 'imdbVotes': '106', 'imdbID': 'tt0291117', 'Type': 'movie', 'DVD': 'N/A', 'BoxOffice': 'N/A', 'Production': 'Cinema Libre', 'Website': 'N/A', 'Response': 'True', 'InternetMovieDatabaseRating': '6.8/10', 'RottenTomatoesRating': 'N/A', 'MetacriticRating': 'N/A'}
1.8602275848388672


2610
https://en.wikipedia.org/w/index.php?title=F%C3%A9lix+et+Lola&action=edit&redlink=1


JSONDecodeError: Expecting value: line 1 column 1 (char 0)

In [8]:
credentials = pd.read_csv('credentials.csv')
omdbapikey = credentials['omdbapikey'][0]
regex_paren = '_\((.*film.*)\)'

# for i in df_festival['id']:
for i in range(2611, len(df_festival['id'])):
    t0 = time.time()
    
    title_link = df_festival.iloc[i]['link_film']
    title_link = title_link.replace('https://en.wikipedia.org/wiki/', '')
    title_link = re.sub(regex_paren, '', title_link.replace('https://en.wikipedia.org/wiki/', ''))
    title_link = title_link.replace('_', '+')
    title_english = df_festival.iloc[i]['title_english'].replace(' ', '+')
    title_original = df_festival.iloc[i]['title_original'].replace(' ', '+')
    print(i)
    print(title_link)
    
    year_festival = df_festival.iloc[i]['year_festival']
    
    film_json = get_film_json(omdbapikey, title_link, title_english, title_original, year_festival)
    film_json = clean_film_json(film_json) if film_json['Response'] == 'True' else film_json
    
    with open('./data/json/' + str(i) + '.json', 'w') as file:
        json.dump(film_json, file)
    
    print(film_json)
    
    response_delay = time.time() - t0
    print(10*response_delay)
    print('\n')
    time.sleep(10*response_delay)
    
# INCORRECT: 2624 Traffic

2611
Betelnut+Beauty
{'Title': 'Betelnut Beauty', 'Year': '2001', 'Rated': 'N/A', 'Released': '19 May 2001', 'Runtime': '105 min', 'Genre': 'Drama, Romance', 'Director': 'Cheng-sheng Lin', 'Writer': 'Cheng-sheng Lin', 'Actors': 'Chen Chang, Angelica Lee, Chen-Nan Tsai, Ming-chun Kao', 'Plot': "A cute coed leaves her mother's home and gets involved with a pastry chef who just finish his military service. The two rebelious youngsters deal with the harsh realities of life on the streets of Taipei by having links to the local criminal element.", 'Language': 'Mandarin, Hokkien', 'Country': 'Taiwan, France', 'Awards': '2 wins & 2 nominations.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BMTQ2MTQ0OTA3Ml5BMl5BanBnXkFtZTgwNjM2MTI3NTE@._V1_SX300.jpg', 'Metascore': 'N/A', 'imdbRating': '6.5', 'imdbVotes': '415', 'imdbID': 'tt0275902', 'Type': 'movie', 'DVD': 'N/A', 'BoxOffice': 'N/A', 'Production': 'N/A', 'Website': 'N/A', 'Response': 'True', 'InternetMovieDatabaseRating': '6.5/10', 'Rotte

2618
https://en.wikipedia.org/w/index.php?title=Kuroe&action=edit&redlink=1
{'Title': 'Kuroe', 'Year': '2001', 'Rated': 'N/A', 'Released': '15 Jun 2001', 'Runtime': '128 min', 'Genre': 'Drama', 'Director': 'Gô Rijû', 'Writer': 'Kôji Hagiuda, Gô Rijû, Boris Vian (novel)', 'Actors': "Masatoshi Nagase, Rie Tomosaka, Shin'ya Tsukamoto, Miyuki Matsuda", 'Plot': 'N/A', 'Language': 'Japanese', 'Country': 'Japan', 'Awards': '3 wins & 1 nomination.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BNzQwNDllMzUtZjZkOS00YmU4LWE4ZGQtYjJjYjZlYTlkNDY5XkEyXkFqcGdeQXVyNTM0MDc1ODE@._V1_SX300.jpg', 'Metascore': 'N/A', 'imdbRating': '6.9', 'imdbVotes': '97', 'imdbID': 'tt0276015', 'Type': 'movie', 'DVD': 'N/A', 'BoxOffice': 'N/A', 'Production': 'N/A', 'Website': 'N/A', 'Response': 'True', 'InternetMovieDatabaseRating': '6.9/10', 'RottenTomatoesRating': 'N/A', 'MetacriticRating': 'N/A'}
5.311071872711182


2619
Little+Senegal
{'Title': 'Little Senegal', 'Year': '2001', 'Rated': 'N/A', 'Released': '18 Ap

2625
https://en.wikipedia.org/w/index.php?title=Weiser&action=edit&redlink=1
{'Title': 'Weiser', 'Year': '2001', 'Rated': 'N/A', 'Released': '18 Jan 2001', 'Runtime': '95 min', 'Genre': 'Drama, Mystery', 'Director': 'Wojciech Marczewski', 'Writer': 'Wojciech Marczewski (scenario), Pawel Huelle (based on the novel by: "Weiser Dawidek"), Maciej Strzembosz (scenario collaborator), Tony Grisoni (scenario collaborator)', 'Actors': 'Marek Kondrat, Krystyna Janda, Juliane Köhler, Teresa Marczewska', 'Plot': 'he hero is Paul Heller, a man who in life was successful. For many years he lived in Hamburg, where he met his wife, and he made quite a pretty good property. After 11 years spent in exile, however, Paul decides to return to the Polish, the country, which since 1989 is the ideal place to start your own profitable business.', 'Language': 'Polish', 'Country': 'Poland, Switzerland, Germany, Denmark, France', 'Awards': '5 wins & 7 nominations.', 'Poster': 'https://m.media-amazon.com/images/M/

2631
Baader
{'Title': 'Baader', 'Year': '2002', 'Rated': 'N/A', 'Released': '17 Oct 2002', 'Runtime': '115 min', 'Genre': 'Biography, Crime, Drama', 'Director': 'Christopher Roth', 'Writer': 'Christopher Roth, Moritz von Uslar', 'Actors': 'Can Taylanlar, Frank Giering, Laura Tonke, Hinnerk Schönemann', 'Plot': 'Andreas Baader starts out as a small-time criminal. In Berlin, he is recruited by a revolutionary cell. They plan to overthrow the state.', 'Language': 'German, English, French, Arabic', 'Country': 'Germany, UK', 'Awards': '1 win & 3 nominations.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BMjI4NDkwMjMzNV5BMl5BanBnXkFtZTgwNTM2NTAzMTE@._V1_SX300.jpg', 'Metascore': 'N/A', 'imdbRating': '5.5', 'imdbVotes': '676', 'imdbID': 'tt0309320', 'Type': 'movie', 'DVD': 'N/A', 'BoxOffice': 'N/A', 'Production': 'N/A', 'Website': 'N/A', 'Response': 'True', 'InternetMovieDatabaseRating': '5.5/10', 'RottenTomatoesRating': 'N/A', 'MetacriticRating': 'N/A'}
2.085700035095215


2632
Bad+Guy


2638
Grill+Point
{'Title': 'Grill Point', 'Year': '2002', 'Rated': 'N/A', 'Released': '03 Oct 2002', 'Runtime': '106 min', 'Genre': 'Comedy, Drama', 'Director': 'Andreas Dresen', 'Writer': 'Andreas Dresen, Cooky Ziesche (dramaturge)', 'Actors': 'Steffi Kühnert, Gabriela Maria Schmeide, Thorsten Merten, Axel Prahl', 'Plot': 'Two pairs, each married for quite a long time, are living in a small east German town. The film focuses on the relationships between each of the four people and what happens when an affair takes place between two of them who are not married to each other and logically betraying the two remaining characters. This event leads to deep thoughts about marriage, friendship, relationships and last not least life itself.', 'Language': 'German', 'Country': 'Germany', 'Awards': '11 wins & 9 nominations.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BMTg1MDM5ODIzMF5BMl5BanBnXkFtZTYwNDk0ODc5._V1_SX300.jpg', 'Metascore': 'N/A', 'imdbRating': '7.2', 'imdbVotes': '1,499', 'i

...

4421
All+That+Jazz
{'Title': 'All That Jazz', 'Year': '1979', 'Rated': 'R', 'Released': '20 Dec 1979', 'Runtime': '123 min', 'Genre': 'Drama, Music, Musical', 'Director': 'Bob Fosse', 'Writer': 'Robert Alan Aurthur, Bob Fosse', 'Actors': 'Roy Scheider, Jessica Lange, Leland Palmer, Ann Reinking', 'Plot': "Choreographing and picking dancers for his current show whilst editing his feature film about a stand-up comedian is getting to Joe Gideon. Without the chemical substances, he would not have the energy to keep up with his girlfriend, his ex-wife, and his special dancing daughter. They attempt to bring him back from the brink, but it's too late for his exhausted body and stress-ravaged heart. He chain-smokes, uses drugs, sleeps with his dancers and overworks himself into open-heart surgery. Scenes from his past life start to encroach on the present and he becomes increasingly aware of his mortality.", 'Language': 'English, Spanish', 'Country': 'USA', 'Awards': 'Won 4 Oscars. Another 7 

4427
Dedicatoria
{'Response': 'False', 'Error': 'Movie not found!'}
5.67983865737915


4428
Ek+Din+Pratidin
{'Response': 'False', 'Error': 'Movie not found!'}
5.6209611892700195


4429
Fantastica
{'Title': 'Fantastica', 'Year': '1980', 'Rated': 'N/A', 'Released': '31 Oct 1980', 'Runtime': '110 min', 'Genre': 'Musical, Drama', 'Director': 'Gilles Carle', 'Writer': 'Gilles Carle', 'Actors': 'Carole Laure, Lewis Furey, Serge Reggiani, Claudine Auger', 'Plot': "In this oddball mix of music and drama, an actress (Carole Laure) in a traveling musical revue is involved with the show's director until she meets and falls for an aging ecological activist. He too is drawn to her, and together they try to stop a factory from being built over an old-growth forest.", 'Language': 'French', 'Country': 'France, Canada', 'Awards': '1 win & 4 nominations.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BODE0NzhiNmItNmRlYS00MjMzLWE0NTMtMjllNmYzODQ4MTRhXkEyXkFqcGdeQXVyNjEzMTg5Njk@._V1_SX300.jpg', 'Meta

4439
Put+on+Ice
{'Response': 'False', 'Error': 'Movie not found!'}
5.888769626617432


4440
Sauve+qui+peut+(la+vie)
{'Title': "Bande-annonce de 'Sauve qui peut (la vie)'", 'Year': '1980', 'Rated': 'N/A', 'Released': 'N/A', 'Runtime': '3 min', 'Genre': 'Short, Drama', 'Director': 'Jean-Luc Godard', 'Writer': 'N/A', 'Actors': 'Nathalie Baye, Jacques Dutronc, Isabelle Huppert', 'Plot': 'N/A', 'Language': 'French', 'Country': 'France', 'Awards': 'N/A', 'Poster': 'https://m.media-amazon.com/images/M/MV5BNjVhNTI1N2UtZmFmOC00OGNiLWI0ZGQtYjM0MDdiMjUxOTdiXkEyXkFqcGdeQXVyNTI2NTY2MDI@._V1_SX300.jpg', 'Metascore': 'N/A', 'imdbRating': 'N/A', 'imdbVotes': 'N/A', 'imdbID': 'tt5235808', 'Type': 'movie', 'DVD': 'N/A', 'BoxOffice': 'N/A', 'Production': 'N/A', 'Website': 'N/A', 'Response': 'True', 'InternetMovieDatabaseRating': 'N/A', 'RottenTomatoesRating': 'N/A', 'MetacriticRating': 'N/A'}
1.2252616882324219


4441
Special+Treatment
{'Response': 'False', 'Error': 'Movie not found!'}
5.507521629333496


4449
A+Somewhat+Gentle+Man
{'Title': 'A Somewhat Gentle Man', 'Year': '2010', 'Rated': 'Not Rated', 'Released': '19 Mar 2010', 'Runtime': '113 min', 'Genre': 'Comedy, Crime, Drama', 'Director': 'Hans Petter Moland', 'Writer': 'Kim Fupz Aakeson (screenplay)', 'Actors': 'Stellan Skarsgård, Jorunn Kjellsby, Bjørn Floberg, Gard B. Eidsvold', 'Plot': "Ulrik is reluctantly let out of prison after serving 12 years for murder. He has to cope with his gang, his ex, a few women - and a snitch. His son has a fiancé. Her family doesn't approve of murder. They have a nursery, they have principles. Ulrik is a somewhat gentle man. But how gentle can you be? ...and he's losing his hair.", 'Language': 'Norwegian, Swedish, Saami', 'Country': 'Norway', 'Awards': '6 wins & 9 nominations.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BMTkxOTI3Njc4MF5BMl5BanBnXkFtZTcwMzI0NTIzNA@@._V1_SX300.jpg', 'Metascore': '68', 'imdbRating': '6.9', 'imdbVotes': '6,405', 'imdbID': 'tt1386683', 'Type': 'movie', 'DVD'

4456
On+the+Path
{'Title': 'On the Path', 'Year': '2010', 'Rated': 'N/A', 'Released': '20 Feb 2010', 'Runtime': '100 min', 'Genre': 'Drama', 'Director': 'Jasmila Zbanic', 'Writer': 'Jasmila Zbanic', 'Actors': 'Zrinka Cvitesic, Leon Lucev, Ermin Bravo, Mirjana Karanovic', 'Plot': 'From Bosnia/Herzegovina: Amar finds a new job working with a community of Muslims. This affects his relationship with his girlfriend Luna as his beliefs begin to change.', 'Language': 'Bosnian', 'Country': 'Bosnia and Herzegovina, Austria, Germany, Croatia', 'Awards': '4 wins & 2 nominations.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BMzA2NjM3NTcxN15BMl5BanBnXkFtZTgwNjk0NzU2MDE@._V1_SX300.jpg', 'Metascore': 'N/A', 'imdbRating': '7.0', 'imdbVotes': '1,601', 'imdbID': 'tt1156531', 'Type': 'movie', 'DVD': 'N/A', 'BoxOffice': 'N/A', 'Production': 'N/A', 'Website': 'N/A', 'Response': 'True', 'InternetMovieDatabaseRating': '7.0/10', 'RottenTomatoesRating': 'N/A', 'MetacriticRating': 'N/A'}
1.29268884658813

In [8]:
with open('./data/json/3.json') as file:
    data = json.load(file)

In [9]:
data

{'Response': 'False', 'Error': 'Movie not found!'}

In [10]:
df = pd.DataFrame(columns = ['Title',
                             'Year',
                             'Rated',
                             'Released',
                             'Runtime',
                             'Genre',
                             'Director', 
                             'Writer',
                             'Actors',
                             'Plot',
                             'Language',
                             'Country',
                             'Awards',
                             'Poster',
                             'Metascore',
                             'imdbRating',
                             'imdbVotes',
                             'imdbID',
                             'Type',
                             'DVD',
                             'BoxOffice',
                             'Production',
                             'Website',
                             'Response',
                             'InternetMovieDatabaseRating',
                             'RottenTomatoesRating',
                             'MetacriticRating'])

In [11]:
df.append(pd.Series(data), ignore_index=True)

Title Year Rated Released Runtime Genre Director Writer Actors Plot  ...  \
0   NaN  NaN   NaN      NaN     NaN   NaN      NaN    NaN    NaN  NaN  ...   

  Type  DVD BoxOffice Production Website Response InternetMovieDatabaseRating  \
0  NaN  NaN       NaN        NaN     NaN    False                         NaN   

  RottenTomatoesRating MetacriticRating             Error  
0                  NaN              NaN  Movie not found!  

[1 rows x 28 columns]